# Используем f2py

Я очень советую воспользоваться [этим гайдом](https://numpy.org/devdocs/f2py/f2py.getting-started.html), он простой и довольно понятный. Давайте посмотрим на пример оттуда:

In [1]:
cat fib1.f

C FILE: FIB1.F
      SUBROUTINE FIB(A,N)
C
C     CALCULATE FIRST N FIBONACCI NUMBERS
C
      INTEGER N
      REAL*8 A(N)
      DO I=1,N
         IF (I.EQ.1) THEN
            A(I) = 0.0D0
         ELSEIF (I.EQ.2) THEN
            A(I) = 1.0D0
         ELSE 
            A(I) = A(I-1) + A(I-2)
         ENDIF
      ENDDO
      END
C END FILE FIB1.F


Теперь надо скомпилировать эту штуку с помощью `f2py`. Если вы используете unix-подобные системы, то все относительно просто, главное не забудьте поставить `gfortran` и `gcc`, дальше вбиваем в командную линию из директории в которой находится этот файл:

`python -m numpy.f2py -c fib1.f -m fib1`

По какой-то причине это выдавало у меня невнятную ошибку, но почему-то заработало от sudo, прада пришлось указать путь к питону, у меня было так:

`sudo /home/teimy/anaconda3/bin/python -m numpy.f2py -c fib1.f -m fib1`

Не знаю, как будет работать у вас, попробуйте оба варианта, главное не забудьте поменять путь к питону так, как он прописан у вас. Если вы не знаете где он, то можно это узнать прописав `which python`.

С windows история чуть более сложная, опять же есть [вот такой гайд](https://scipy.github.io/old-wiki/pages/F2PY_Windows.html), а если он не поможет, то [этот ответ на стаковерфлоу](https://stackoverflow.com/questions/48826283/compile-fortran-module-with-f2py-and-python-3-6-on-windows-10). 

Теперь у нас есть файл `fib1.so` (или что-то в этом духе, у меня вот `fib1.cpython-37m-x86_64-linux-gnu.so`), который является своеобразным модулем, в котором находятся все функции из файла `fib1.f`. Посмотрим как он работает:

In [2]:
import fib1
import numpy as np

In [3]:
a = np.zeros(8)
fib1.fib(a, 8)

In [4]:
a

array([ 0.,  1.,  1.,  2.,  3.,  5.,  8., 13.])

В целом оно работает! Но немного непривычно, я как-то привык что функция что-то возвращает. На самом деле такая схема ~~почти никогда не~~ не всегда работает, поэтому надо размечать аргументы функции в самом файле. Вот так:

In [5]:
cat fib3.f

C FILE: FIB3.F
      SUBROUTINE FIB(A,N)
C
C     CALCULATE FIRST N FIBONACCI NUMBERS
C
      INTEGER N
      REAL*8 A(N)
Cf2py intent(in) n
Cf2py intent(out) a
Cf2py depend(n) a
      DO I=1,N
         IF (I.EQ.1) THEN
            A(I) = 0.0D0
         ELSEIF (I.EQ.2) THEN
            A(I) = 1.0D0
         ELSE 
            A(I) = A(I-1) + A(I-2)
         ENDIF
      ENDDO
      END
C END FILE FIB3.F

Так как первый символ строки C, то fortran будет считать эту строку комменатарием, и будет ее игнорировать, а вот cython ее читает и запоминает. Посмотрим:

In [6]:
import fib3
fib3.fib(8)

array([ 0.,  1.,  1.,  2.,  3.,  5.,  8., 13.])

Перейдем к более серьезным примерам. Возьмем целый набор функций `spher.f`:

In [7]:
cat spher_test.f


C  The program computes far-field light scattering by polydisperse     
C  homogeneous spherical particles using the Lorenz-Mie theory.    
                                                                     
C  Last modified 08/06/2005                                            
                                                                        
C  The program is based on the book                                    
C 
C  1. Mishchenko, M. I., L. D. Travis, and A. A. Lacis (2002). 
C     Scattering, Absorption, and Emission of Light
C     by Small Particles. Cambridge University Press, Cambridge.
C
C  The book is available in the .pdf format at the following
C  web site:
C
C   http://www.giss.nasa.gov/~crmim/books.html
C                                                                      
C  One can also use the following paper as a brief user guide:               
C                                                                      
C  2. M. I. Mishchenko, J. M. Dlugach, E.

In [8]:
import spher_test

Пропишем какие-нибудь дефолотные аргументы, чтобы убедиться в работспособности:

In [9]:
r1 = 0.1
r2 = 10
ndistr = 2 # log-normal disribution
aa = 1 # mean radius of distribution, let us say in microns
bb = np.log(0.7)**2 # geom_std here is geometrical std. dev
gam = 1 # most likely you do not need in case of log distr this one but who knows?
lam = 1.3 # lambda in microns
mrr = 1.5 # real part of refr. index
mrii = 0.01 # im. part of refr. index
n = 100 # number of integration subintervals on the interval (R1, R2)  of particle radii 
        # 100 was in example, and it works good
        # note that r1 and r2 seriously affect this parameter
npp = 1000 # for power law  
nk = 5 # number of gaussian division points. looks legit at 3.
# npna = 10 # also dont know what is good value
# next parameters should be useless:
area = 0 # ??? 
volume = 0 # ????
rvw = 0 # ??
rmean = 0 # ???
bb2 = 0 #????
bb1 = 0 #???
aa1 = 0 #???
aa2 = 0 #???
ddelt = 1e-14 # I do not know how exactly it affects computations.

L1 = 0
AL1 = 0 
AL2 = 0
AL3 = 0
AL4 = 0
BET1 = 0
BET2 = 0
CEXT = 0
CSCA = 0

In [10]:
l1,al1,al2,al3,al4,bet1,bet2,cext,csca = spher_test.spher(aa,bb,gam,lam,mrr,mrii,r1,r2,n,npp,ndistr,nk,area,volume,rvw,rmean,aa1,bb1,aa2,bb2,ddelt)

In [11]:
csca/cext

0.8947042815350186

Если вы не хотите таскать `.so` файл из проекта в проект, то можете его закинуть `/home/user/anaconda3/bin`, ну или туда где у вас стоит anaconda.

Как еще можно упростить свою жизнь? Я написал простую обертку этой функции, чтобы не вызывать ее каждый раз с миллионом аргументов и чтобы это было читаемо. Вариант для лог-нормального распределения:

In [36]:
from spher_test import spher
def lognormal_mish(wvl, n_r, n_i, grain, r1=None, r2=None, geom_std=0.7):
    """Code for calculating SSAs and extinction coefficients for particle mixtures.
    
    It uses Mishenko code for scattering on number of spheres, in this case, size distribution
    of spheres is lognormal.
    
    Parameters
    ----------
    wvl : float
        Wavelength in microns.
    n_r : float
        Real part of refracative index. 
    n_i : float
        Imaginary part of refracative index. 
    grain : float
        Mean radius of grain size in distribution, in microns.
    r1 : float
        From this size you will start integrating.
    r2 : float
        And at this size you will end integrating.
    geom_std : float
        This is the geometrical std of the lognormal distribution, unitless.
    """
    if r1 is None:
        r1 = grain/10
    if r2 is None:
        r2 = grain*10
    
    ndistr = 2 # log-normal disribution
    aa = grain # mean radius of distribution, let us say in microns
    bb = np.log(geom_std)**2 # geom_std here is geometrical std. dev
    gam = 1 # most likely you do not need in case of log distr this one but who knows?
    lam = wvl # lambda in microns
    mrr = n_r # real part of refr. index
    mrii = n_i # im. part of refr. index
    n = 100 # number of integration subintervals on the interval (R1, R2)  of particle radii 
            # 100 was in example, and it works good
            # note that r1 and r2 seriously affect this parameter
    npp = 1000 # for power law  
    nk = 5 # number of gaussian division points. looks legit at 3.
    # npna = 10 # also dont know what is good value
    # next parameters should be useless:
    area = 0 # ??? 
    volume = 0 # ????
    rvw = 0 # ??
    rmean = 0 # ???
    bb2 = 0 #????
    bb1 = 0 #???
    aa1 = 0 #???
    aa2 = 0 #???
    ddelt = 1e-14 # I do not know how exactly it affects computations.
    
    if np.isscalar(wvl):
        l1,al1,al2,al3,al4,bet1,bet2,cext,csca = spher(aa,bb,gam,lam,mrr,
                                                             mrii,r1,r2,n,npp,ndistr,
                                                             nk,area,volume,rvw,rmean,
                                                             aa1,bb1,aa2,bb2,ddelt)
        return float(cext), float(csca), float(al1[1]/3)
    elif np.isscalar(wvl)==False:
        raise ValueError('Please put scalar value in inputs.')

In [29]:
lognormal_mish(1, 1, 0.001, 0.1, r1=0.01, r2=10, geom_std=0.7)

(9.318219310387437e-05, 2.9268426459236973e-08, 0.27849833215366276)

Клево, но это ведь очень невекторизованная программа, давайте сделаем с этим что-нибудь! Так как каждая итерация этой программы не зависит от любых других, он очень просто параллелится. Параллелить что-либо в питоне очень просто, так как существует огромное количество решений, начиная от традицонных OpenMP и MPI, заканчивая pyCUDA. Но OpenMP и MPI это вообще сложно (те кто работал с ними поймут), а мы не любми сложных решений, поэтому мы делаем следующее:

In [49]:
ray.shutdown()

In [50]:
import ray

ray.init(num_cpus=16)

@ray.remote(memory=100 * 1024 * 1024)
def mishray(wvl, n_r, n_i, grain, geom_std=0.7):
    cext, csca, g = lognormal_mish(wvl, n_r, n_i, grain=grain, r1=None, r2=None, geom_std=geom_std)
    return cext, csca, g

sample_ray = []
wvl_grid = np.linspace(1,2,1000)
n_ks = np.linspace(1,1,100)
n_is = np.abs(np.sin(wvl_grid))*0.01 + 0.005
for i in range(len(wvl_grid)):
    sample_ray.append(mishray.remote(1, 1, 0.01, 10, 0.7))
sample = ray.get(sample_ray)

ray.shutdown()



2020-10-27 16:29:47,523	WARNING services.py:586 -- setpgrp failed, processes may not be cleaned up properly: [Errno 1] Operation not permitted.
2020-10-27 16:29:47,524	INFO resource_spec.py:212 -- Starting Ray with 8.69 GiB memory available for workers and up to 4.35 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-10-27 16:29:47,752	INFO services.py:1078 -- View the Ray dashboard at localhost:8265


(pid=54443) LOG NORMAL DISTRIBUTION, r_g= 10.0000  [ln(sigma_g)]**2=0.1272
(pid=54443) R1 =0.100000D+01   R2=0.100000D+03
(pid=54443) REFF=0.137443D+02   VEFF=0.135663D+00
(pid=54443) LAM =  1.0000  MRR=  1.000  MRI= 0.01000
(pid=54443) NK=   5   N= 100   NP=1000
(pid=54443) <COS> =0.998973D+00
(pid=54443) CEXT=0.511591D+03   CSCA=0.175300D+03   ALBEDO =0.342658D+00
(pid=54443) MAXIMAL ORDER OF MIE COEFFICIENTS =  671
(pid=54443)  
(pid=54443) *********   EXPANSION COEFFICIENTS   *********
(pid=54443)    S     ALPHA 1    ALPHA 2    ALPHA 3    ALPHA 4     BETA 1     BETA 2
(pid=54443)    0     1.00000    0.00000    0.00000    0.99988    0.00000   -0.00000
(pid=54443)    1     2.99692    0.00000    0.00000    2.99690    0.00000   -0.00000
(pid=54443)    2     4.98581    4.99505    4.99486    4.98579    0.00052    0.00000
(pid=54443)    3     6.96265    6.97424    6.97410    6.96263    0.00086   -0.00001
(pid=54443)    4     8.92436    8.93797    8.93786    8.92434    0.00120   -0.00003
(

(pid=54440)  673     0.00255    0.00255    0.00255    0.00255    0.00000   -0.00000
(pid=54440)  674     0.00251    0.00251    0.00251    0.00251    0.00000   -0.00000
(pid=54440)  675     0.00247    0.00247    0.00247    0.00247    0.00000   -0.00000
(pid=54440)  676     0.00243    0.00243    0.00243    0.00243    0.00000   -0.00000
(pid=54440)  677     0.00238    0.00238    0.00238    0.00238    0.00000   -0.00000
(pid=54440)  678     0.00234    0.00234    0.00234    0.00234    0.00000   -0.00000
(pid=54440)  679     0.00231    0.00231    0.00231    0.00231    0.00000   -0.00000
(pid=54440)  680     0.00227    0.00227    0.00227    0.00227    0.00000   -0.00000
(pid=54440)  681     0.00223    0.00223    0.00223    0.00223    0.00000   -0.00000
(pid=54440)  682     0.00219    0.00219    0.00219    0.00219    0.00000   -0.00000
(pid=54440)  683     0.00216    0.00216    0.00216    0.00216    0.00000   -0.00000
(pid=54440)  684     0.00212    0.00212    0.00212    0.00212    0.00000   -

2020-10-27 16:29:50,574	WARNING worker.py:956 -- The driver may not be able to keep up with the stdout/stderr of the workers. To avoid forwarding logs to the driver, use 'ray.init(log_to_driver=False)'.



(pid=54447) 1225     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1226     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1227     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1228     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1229     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1230     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1231     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1232     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1233     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1234     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1235     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54447) 1236     0.00000    0.00000    0.00000    0.00000    0.00000   

...


(pid=54449)  337     1.21052    1.21068    1.21068    1.21052    0.00151   -0.00060
(pid=54449)  338     1.18723    1.18739    1.18739    1.18723    0.00149   -0.00059
(pid=54449)  339     1.16439    1.16455    1.16455    1.16439    0.00146   -0.00058
(pid=54449)  340     1.14199    1.14214    1.14214    1.14199    0.00143   -0.00057
(pid=54449)  341     1.12003    1.12017    1.12017    1.12003    0.00140   -0.00056
(pid=54449)  342     1.09848    1.09863    1.09862    1.09848    0.00138   -0.00055
(pid=54449)  343     1.07735    1.07749    1.07749    1.07735    0.00135   -0.00054
(pid=54449)  344     1.05663    1.05677    1.05677    1.05663    0.00132   -0.00053
(pid=54449)  345     1.03631    1.03645    1.03645    1.03631    0.00130   -0.00052
(pid=54449)  346     1.01638    1.01652    1.01651    1.01638    0.00128   -0.00051
(pid=54449)  347     0.99684    0.99697    0.99697    0.99684    0.00125   -0.00050
(pid=54449)  348     0.97768    0.97780    0.97780    0.97768    0.00123   

(pid=54444)  215    12.33183   12.33443   12.33441   12.33183    0.01350   -0.00467
(pid=54444)  216    12.11200   12.11453   12.11452   12.11199    0.01329   -0.00461
(pid=54444)  217    11.89570   11.89818   11.89816   11.89569    0.01308   -0.00454
(pid=54444)  218    11.68289   11.68532   11.68530   11.68289    0.01287   -0.00447
(pid=54444)  219    11.47353   11.47590   11.47589   11.47353    0.01267   -0.00441
(pid=54444)  220    11.26757   11.26990   11.26988   11.26757    0.01247   -0.00434
(pid=54444)  221    11.06498   11.06725   11.06724   11.06498    0.01227   -0.00428
(pid=54444)  222    10.86571   10.86793   10.86792   10.86571    0.01207   -0.00422
(pid=54444)  223    10.66972   10.67189   10.67188   10.66972    0.01188   -0.00416
(pid=54444)  224    10.47696   10.47909   10.47907   10.47696    0.01169   -0.00409
(pid=54444)  225    10.28740   10.28947   10.28946   10.28739    0.01150   -0.00403
(pid=54444)  226    10.10098   10.10301   10.10300   10.10098    0.01131   -

(pid=54441) 1141     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1142     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1143     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1144     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1145     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1146     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1147     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1148     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1149     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1150     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1151     0.00000    0.00000    0.00000    0.00000    0.00000   -0.00000
(pid=54441) 1152     0.00000    0.00000    0.00000    0.00000    0.00000   -

(pid=54438)  279     3.72227    3.72288    3.72288    3.72227    0.00448   -0.00167
(pid=54438)  280     3.65142    3.65202    3.65201    3.65142    0.00440   -0.00165
(pid=54438)  281     3.58189    3.58247    3.58247    3.58189    0.00432   -0.00162
(pid=54438)  282     3.51365    3.51422    3.51421    3.51365    0.00425   -0.00159
(pid=54438)  283     3.44668    3.44724    3.44723    3.44668    0.00417   -0.00156
(pid=54438)  284     3.38096    3.38150    3.38150    3.38096    0.00409   -0.00154
(pid=54438)  285     3.31647    3.31700    3.31699    3.31647    0.00402   -0.00151
(pid=54438)  286     3.25318    3.25370    3.25369    3.25318    0.00394   -0.00148
(pid=54438)  287     3.19107    3.19158    3.19158    3.19107    0.00387   -0.00146
(pid=54438)  288     3.13013    3.13063    3.13062    3.13013    0.00380   -0.00143
(pid=54438)  289     3.07033    3.07081    3.07081    3.07033    0.00373   -0.00141
(pid=54438)  290     3.01165    3.01212    3.01212    3.01165    0.00366   -

2020-10-27 16:29:55,412	WARNING worker.py:956 -- The driver may not be able to keep up with the stdout/stderr of the workers. To avoid forwarding logs to the driver, use 'ray.init(log_to_driver=False)'.
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

